In [1]:
import gtrace.beam as beam  # Gaussian beam module
import gtrace.optcomp as opt  # Optical components
import gtrace.draw as draw  # A module to draw results into CAD files
from gtrace.draw.tools import drawAllBeams, drawAllOptics, transAll, rotateAll #Utility functions for drawing 
import gtrace.draw.renderer as renderer
from gtrace.unit import *  # A convenience module to represent various modules
import gtrace.optics.gaussian as gauss # A utility module for Gaussian beams
from gtrace.nonsequential import non_seq_trace #Non-sequential trace
from gtrace.optics.geometric import vector_normalize #A function to normalize a vector

import numpy as np  #Numpy
pi = np.pi  #Just for brevity

In [40]:
#q-parameter of the beam
q0 = gauss.Rw2q(ROC=np.inf, w=0.3*mm)

#Create a GaussianBeam object.
b0 = beam.GaussianBeam(q0=q0, wl=1550*nm, length=500*cm, P=1.0)

#Set the direction angle of the beam to 10deg from the global x-axis.
b0.dirAngle = deg2rad(0)

#Set the position of the origin of the beam
b0.pos = (0, 23*2.54*cm)

In [85]:
M1 = opt.Mirror(HRcenter=[48*2.54*cm, 23*2.54*cm], normAngleHR=deg2rad(225), 
                 diameter=2.54*cm, thickness=.2*cm,
                 wedgeAngle=deg2rad(.2), inv_ROC_HR= 0.0,
                 inv_ROC_AR=0,
                 Refl_HR=0.99, Trans_HR=1-0.99,
                 Refl_AR=500*ppm, Trans_AR=1-500*ppm,
                 n=1.45, name='M1')

M2 = opt.Mirror(HRcenter=[48*2.54*cm, 15*2.54*cm], normAngleHR=deg2rad(135),
                 diameter=2.54*cm, thickness=.2*cm,
                 wedgeAngle=deg2rad(.2), inv_ROC_HR= 0.0,
                 inv_ROC_AR=0,
                 Refl_HR=0.99, Trans_HR=1-0.99,
                 Refl_AR=500*ppm, Trans_AR=1-500*ppm,
                 n=1.45, name='M2')
FCM1 = opt.Mirror(HRcenter=[31*2.54*cm, 15*2.54*cm], normAngleHR=deg2rad(3),
                 diameter=2.54*cm, thickness=.2*cm,
                 wedgeAngle=deg2rad(.2), inv_ROC_HR= 0.0,
                 inv_ROC_AR=0,
                 Refl_HR=1-883e-6, Trans_HR=883e-6,
                 Refl_AR=500*ppm, Trans_AR=1-500*ppm,
                 n=1.45, name='FCM1')
FCM2 = opt.Mirror(HRcenter=[7.442*2.54*cm, 15*2.54*cm], normAngleHR=deg2rad(-3),
                 diameter=2.54*cm, thickness=.2*cm,
                 wedgeAngle=deg2rad(.2), inv_ROC_HR= 0.0,
                 inv_ROC_AR=0,
                 Refl_HR=1-883e-6, Trans_HR=883e-6,
                 Refl_AR=500*ppm, Trans_AR=1-500*ppm,
                 n=1.45, name='FCM2')
FCM3 = opt.Mirror(HRcenter=[31*2.54*cm, 12.674*2.54*cm], normAngleHR=deg2rad(177),
                 diameter=2.54*cm, thickness=.2*cm,
                 wedgeAngle=deg2rad(.2), inv_ROC_HR= 1/(160*cm),
                 inv_ROC_AR=0,
                 Refl_HR=1-1e-6, Trans_HR=1e-6,
                 Refl_AR=500*ppm, Trans_AR=1-500*ppm,
                 n=1.45, name='FCM3')
FCM4 = opt.Mirror(HRcenter=[7.442*2.54*cm, 12.674*2.54*cm], normAngleHR=deg2rad(3),
                 diameter=2.54*cm, thickness=.2*cm,
                 wedgeAngle=deg2rad(.2), inv_ROC_HR= 1/(160*cm),
                 inv_ROC_AR=0,
                 Refl_HR=1-1e-6, Trans_HR=1e-6,
                 Refl_AR=500*ppm, Trans_AR=1-500*ppm,
                 n=1.45, name='FCM4')
FCM1_2 = opt.Mirror(HRcenter=[31*2.54*cm, 15*2.54*cm], normAngleHR=deg2rad(183),
                 diameter=2.54*cm, thickness=.2*cm,
                 wedgeAngle=deg2rad(.2), inv_ROC_HR= 0.0,
                 inv_ROC_AR=0,
                 Refl_HR=1-883e-6, Trans_HR=883e-6,
                 Refl_AR=500*ppm, Trans_AR=1-500*ppm,
                 n=1.45, name='FCM1_2')


In [88]:
beamDict = {}

beams = M1.hitFromHR(b0, order=2)
print(beams)
#Save the incident beam to the beam dictionary
beamDict['input_beam'] = beams['input']

#Save other beams
beamDict['M1s1'] = beams['s1']
beamDict['M1t1'] = beams['t1']
beamDict['M1s2'] = beams['s2']
beamDict['M1s3'] = beams['s3']
beamDict['M1t2'] = beams['t2']

#Reflected beam from M1
b = beams['r1']

#Hit M2
beams = M2.hitFromHR(b, order=2)
print(beams)
#Save the beam from M1 to M2
beamDict['M1toM2'] = beams['input']
beamDict['M2s1'] = beams['s1']
beamDict['M2t1'] = beams['t1']

#Reflected beam from M2
b = beams['r1']

#Hit first FC mirror
beams = FCM1.hitFromHR(b, order=2)
print(beams)
beamDict['M2toFCM1'] = beams['input']
beamDict['FCM1s1'] = beams['s1']
beamDict['FCM1t1'] = beams['t1']

b = beams['t1']
#Hit second FC mirror
beams = FCM2.hitFromHR(b, order=2)
print(beams)
beamDict['FCM1toFCM2'] = beams['input']
beamDict['FCM2s2'] = beams['s1']
beamDict['FCM2t1'] = beams['t1']

b = beams['r1']
#Hit third FC mirror
beams = FCM3.hitFromHR(b, order=2)
print(beams)
beamDict['FCM2toFCM3'] = beams['input']
beamDict['FCM3s2'] = beams['s1']
beamDict['FCM3t1'] = beams['t1']

b = beams['r1']
#Hit fourth FC mirror
beams = FCM4.hitFromHR(b, order=2)
print(beams)
beamDict['FCM3toFCM4'] = beams['input']
beamDict['FCM4s2'] = beams['s1']
beamDict['FCM4t1'] = beams['t1']

b = beams['r1']
#Hit 1st FC mirror
beams = FCM1_2.hitFromHR(b, order=2)
print(beams)
beamDict['FCM4toFCM1_2'] = beams['input']
beamDict['FCM1_2s2'] = beams['s1']
beamDict['FCM1_2t1'] = beams['t1']



{'input': <gtrace.beam.GaussianBeam object at 0x000002F236098130>, 'r1': <gtrace.beam.GaussianBeam object at 0x000002F236155040>, 's1': <gtrace.beam.GaussianBeam object at 0x000002F23596E0E0>, 't1': <gtrace.beam.GaussianBeam object at 0x000002F2361553B0>, 's2': <gtrace.beam.GaussianBeam object at 0x000002F236155090>, 's3': <gtrace.beam.GaussianBeam object at 0x000002F2360C4CC0>, 't2': <gtrace.beam.GaussianBeam object at 0x000002F236155450>}
{'input': <gtrace.beam.GaussianBeam object at 0x000002F236098EA0>, 'r1': <gtrace.beam.GaussianBeam object at 0x000002F23614E9A0>, 's1': <gtrace.beam.GaussianBeam object at 0x000002F2360C20E0>, 't1': <gtrace.beam.GaussianBeam object at 0x000002F2360C6720>, 's2': <gtrace.beam.GaussianBeam object at 0x000002F236145EA0>, 's3': <gtrace.beam.GaussianBeam object at 0x000002F2361450E0>, 't2': <gtrace.beam.GaussianBeam object at 0x000002F2360C6EF0>}
{'input': <gtrace.beam.GaussianBeam object at 0x000002F235A19220>, 'r1': <gtrace.beam.GaussianBeam object at 0

In [89]:
#Create a canvas object
cnv = draw.Canvas()

#Add a layer to the canvas
cnv.add_layer("main_beam", color=(0,0,0))

#Draw all the beams in beamDict
drawAllBeams(cnv, list(beamDict.values()), drawWidth=True, sigma=3.0, drawPower=False,
                 drawROC=False, drawGouy=False, drawOptDist=False, layer='main_beam',
                    fontSize=0.01)

#Draw the mirror
drawAllOptics(cnv, [M1,M2,FCM1,FCM2,FCM3,FCM4])

#Save the result as a DXF file
renderer.renderDXF(cnv, 'SeqTrace.dxf')